<a href="https://colab.research.google.com/github/Murcha1990/ML_AI25/blob/main/Hometasks/Pro/AI_HW1_Regression_with_inference_pro.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

# **Домашнее задание №1 (pro). Часть 1**

В этом домашнем задании (его первой части) вам будет необходимо:
*  обучить модель регрессии для предсказания стоимости автомобилей;


> Оценка за первую часть домашки = $min(\text{ваш балл}, 7)$



**Примечание**

В каждой части оцениваются как код, **так и ответы на вопросы.** Вопросы подсвечены синим цветом.

Если нет одного и/или другого, то часть баллов за соответствующее задание снимается.

In [3]:
import os
import re
import warnings
import random

import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import seaborn as sns
import phik
import pickle
from phik import phik_matrix
from ydata_profiling import ProfileReport

from sklearn.compose import ColumnTransformer
from sklearn.preprocessing import OneHotEncoder, MinMaxScaler, StandardScaler, PolynomialFeatures
from sklearn.linear_model import ElasticNet, Lasso, LinearRegression, Ridge
from sklearn.metrics import r2_score, mean_squared_error as MSE
from sklearn.model_selection import GridSearchCV, train_test_split

warnings.filterwarnings("ignore")

random.seed(42)
np.random.seed(42)


### **Задание 0**
Давайте зафиксируем важный момент.

**Задание 0 (0 баллов).**
Изучите и ответье на вопрос: для чего фиксируем сиды в домашках?

`Your answer here` Сиды фиксируем для воспроизводимости результатов

# **Часть 1 | EDA**


Первая часть состоит из классических шагов EDA:

- Базовый EDA и обработка признаков (1.7 балла)
- Визуализации признаков и их анализ (1.6 балл)

Всего можно набрать 3.3 основных балла и 0.25 бонусных.

В следующих частях, вы увидите бонусные задания. Бонусные задания выделены как **Дополнительное задание/Бонус**. Вы можете выполнять их, чтобы в случае ошибок в основных задачах всё равно набрать за работу максимум. Кроме того, дополнительные задания позволяют вам углубить знания.

Призываем активно использовать их!

## **Простейший EDA и обработка признаков (1.7 балла)**

In [4]:
df_train = pd.read_csv('https://raw.githubusercontent.com/Murcha1990/MLDS_ML_2022/main/Hometasks/HT1/cars_train.csv')
df_test = pd.read_csv('https://raw.githubusercontent.com/Murcha1990/MLDS_ML_2022/main/Hometasks/HT1/cars_test.csv')

print("Train data shape:", df_train.shape)
print("Test data shape: ", df_test.shape)

Train data shape: (6999, 13)
Test data shape:  (1000, 13)


### **Задание 1.(0.4 балла)**
Выполните операции, направленные на базовое исследование данных:

- [ ] Посмотрите, есть ли в датасете пропуски и дубликаты. Запишите/выведите названия колонок, для которых есть пропущенные значения (0.1 балла)
- [ ] Посмотрите, есть ли в данных явные дубликаты (0.05 балла)
- [ ] Постройте дашборд в одну строку, используя [ydata-profilling](https://github.com/ydataai/ydata-profiling)(0.15 балла)
- [ ] Опишите базовые выводы (какие — выберите сами), используя дашборд (0.2 балла).

In [5]:
# Пропуски
missing_cols_train = df_train.columns[df_train.isnull().any()].tolist()
missing_cols_test = df_test.columns[df_test.isnull().any()].tolist()

print("Колонки с пропусками:")
print(f"Train: {missing_cols_train}")
print(f"Test: {missing_cols_test}")

# Дубликаты
print(f"\nДубликаты: train - {df_train.duplicated().sum()}, test - {df_test.duplicated().sum()}")

Колонки с пропусками:
Train: ['mileage', 'engine', 'max_power', 'torque', 'seats']
Test: ['mileage', 'engine', 'max_power', 'torque', 'seats']

Дубликаты: train - 985, test - 62


In [6]:
# Пропуски по каждому датасету
def check_missing(df, name):
    missing = df.isnull().sum()
    missing = missing[missing > 0]
    print(f"{name} пропуски:")
    for col, count in missing.items():
        print(f"  {col}: {count} ({count/len(df)*100:.1f}%)")
    if missing.empty:
        print("  Нет пропусков")

check_missing(df_train, "Train")
print("-------------------------")
check_missing(df_test, "Test")

Train пропуски:
  mileage: 202 (2.9%)
  engine: 202 (2.9%)
  max_power: 196 (2.8%)
  torque: 203 (2.9%)
  seats: 202 (2.9%)
-------------------------
Test пропуски:
  mileage: 19 (1.9%)
  engine: 19 (1.9%)
  max_power: 19 (1.9%)
  torque: 19 (1.9%)
  seats: 19 (1.9%)


In [7]:
# Дашборд по обьедененным данным для того, что бы понимать общее положение дел в данных
# Можно было бы и по отдельности сделат, но эт информативно и тяжело сравнивать дэш между собой
profile = ProfileReport(pd.concat([df_train, df_test], ignore_index=True),
                        title="Train Dataset",
                        minimal=False,
                        explorative=True)
profile.to_file("report.html")

Summarize dataset:   0%|          | 0/5 [00:00<?, ?it/s]

Generate report structure:   0%|          | 0/1 [00:00<?, ?it/s]

Render HTML:   0%|          | 0/1 [00:00<?, ?it/s]

Export report to file:   0%|          | 0/1 [00:00<?, ?it/s]

In [8]:
profile

In [9]:
# Базовые выводы
print(f"\nРазмеры: train {df_train.shape}, test {df_test.shape}")
print(f"Типы данных:\n{df_train.dtypes.value_counts()}")
if missing_cols_train:
    print(f"Наибольшие пропуски: {df_train[missing_cols_train].isnull().mean().max():.1%}")


Размеры: train (6999, 13), test (1000, 13)
Типы данных:
object     9
int64      3
float64    1
Name: count, dtype: int64
Наибольшие пропуски: 2.9%


**Ваш ответ здесь.**
В целом видно, что основные пропуски находятся в 5 колонках:
- mileage
- engine
- max_power
- torque
- seats

В целом, ~3% строк с пропусками в трейн и 2% в тесте в этих колонках. Это не так критично. В дальнейшем примим решение: **удаление** или **заполнение**

Если брать те признаки, которые не нужно отдельно предобрабатывать (например mileage, engine, max_power и torque нужно конвертировать), есть большой дисабаланс классов. Это мы можем учесть в дальнейшем инжинеринге

### **Задание 2 (0.2 балла)**
Проанализируйте статистики датасета.

**Ваша задача:**
- [ ] Посчитайте основные статистики по числовым столбцам для трейна и теста
- [ ] Посчитайте основные статистики по категориальным столбцам для трейна и теста
- [ ] Сравните среднее и медиану внутри `train`, внутри `test` и между собой. О чём могут говорить результаты?
- [ ] Сделайте выводы по статистикам. Отсутсвие выводов равносильно по баллам невыполнению задания.

**Подсказка:**

Используте ``.describe()`` с нужным(и) аргументом(-ами).

In [10]:
num_cols_train = df_train.select_dtypes(include=['int64', 'float64']).columns
cat_cols_train = df_train.select_dtypes(include=['object', 'category']).columns

num_cols_test = df_test.select_dtypes(include=['int64', 'float64']).columns
cat_cols_test = df_test.select_dtypes(include=['object', 'category']).columns

# 1. Общие сведения
print("Числовые столбцы train:", list(num_cols_train))
print("Категориальные столбцы train:", list(cat_cols_train))
print("-----------------------------------")
print("Числовые столбцы test:", list(num_cols_test))
print("Категориальные столбцы test:", list(cat_cols_test))

print("-----------------------------------")

# 2. Основные статистики числовых колонок
print("Числовые статистики TRAIN")
num_stats_train = df_train[num_cols_train].describe().T
print(num_stats_train)

print("Числовые статистики TEST")
num_stats_test = df_test[num_cols_test].describe().T
print(num_stats_test)

print("-----------------------------------")

# 3. Статистики категориальных признаков
print("Категориальные статистики TRAIN")
cat_stats_train = df_train[cat_cols_train].describe().T
print(cat_stats_train)

print("Категориальные статистики TEST")
cat_stats_test = df_test[cat_cols_test].describe().T
print(cat_stats_test)


# 4. Сравнение среднего и медианы
comparison_df = pd.DataFrame({
    "mean_train": df_train[num_cols_train].mean(),
    "median_train": df_train[num_cols_train].median(),
    "mean_test": df_test[num_cols_test].mean(),
    "median_test": df_test[num_cols_test].median(),
})

comparison_df["mean_diff(train-test)"] = comparison_df["mean_train"] - comparison_df["mean_test"]
comparison_df["median_diff(train-test)"] = comparison_df["median_train"] - comparison_df["median_test"]

print("Сравнение среднего и медианы")
print(comparison_df)


Числовые столбцы train: ['year', 'selling_price', 'km_driven', 'seats']
Категориальные столбцы train: ['name', 'fuel', 'seller_type', 'transmission', 'owner', 'mileage', 'engine', 'max_power', 'torque']
-----------------------------------
Числовые столбцы test: ['year', 'selling_price', 'km_driven', 'seats']
Категориальные столбцы test: ['name', 'fuel', 'seller_type', 'transmission', 'owner', 'mileage', 'engine', 'max_power', 'torque']
-----------------------------------
Числовые статистики TRAIN
                count           mean            std      min       25%  \
year           6999.0    2013.818403       4.053095   1983.0    2011.0   
selling_price  6999.0  639515.197171  808941.911915  29999.0  254999.0   
km_driven      6999.0   69584.615517   57724.001817      1.0   35000.0   
seats          6797.0       5.419008       0.965767      2.0       5.0   

                    50%       75%         max  
year             2015.0    2017.0      2020.0  
selling_price  450000.0  675000

**Выводы:** \
**По средним и медианам:**
- Train и test распределены очень похоже, существенных перекосов нет.

Незначительные отличия:
- В train машины чуть новее и дороже.
- В test машины чуть больше проехали.

Поскольку различия в среднем и медиане близки по масштабу для каждого признака можно сказать, что:
- Сильных выбросов нет (если бы они были, среднее превосходило бы медиану гораздо сильнее).
- Распределения умеренно симметричные или одинаково смещённые.

**В целом:**
Распределения train и test почти совпадают, но есть отличия: test содержит чуть более старые машины с пробегом и низкими ценами (в целом, на игрушечном датасете это не будет проблемой, тем не менее, в бою, при разделении на тест и трейн стоило бы сделать некую стратификацию по по году машины, что бы у нас в тест/трейн не западали тачки одногодки). Выбросы имеются в обоих датасетах (особенно в selling_price и km_driven).
Категориальные признаки в train и test распределены однородно, без сильного распределительного сдвига. Однако большое количество уникальных строковых значений требует очистки, нормализации, выделения числовых компонент (например, из engine, mileage, max_power, torque).

### **Задание 3 (0.2 балла)**

- [ ] Посмотрите, есть ли в трейне объекты с одинаковым признаковым описанием (целевую переменную следует исключить). Если есть, то сколько? (0.01 балла)
- [ ] Отобразите такие объекты (0.01 балла)
- [ ] Удалите повторяющиеся строки. Если при одинаковом признаковом описании цены на автомобили отличаются, то оставьте первую строку по этому автомобилю (0.01 балла)
- [ ]  Обновите индексы строк таким образом, чтобы они шли от 0 без пропусков (0.01 балла)
- [ ] Подумайте, могут ли в данных быть другие скрытые дубли? Предложите, как их можно отлавливать. (0.16 балла)

P.S тут данные без подвоха, но выводы нам нужны.

In [11]:
# Целевая переменная
target_col = 'selling_price'
feature_cols = df_train.columns.drop(target_col)
duplicate_mask = df_train.duplicated(subset=feature_cols, keep=False)
duplicates = df_train[duplicate_mask]

print("Количество объектов с одинаковым описанием признаков:", duplicates.shape[0])
duplicates.head(7)


Количество объектов с одинаковым описанием признаков: 1799


name  year  selling_price  km_driven    fuel  \
22           Maruti Baleno Delta 1.2  2016         575000      45000  Petrol   
26       Maruti Omni E MPI STD BS IV  2018         254999      25000  Petrol   
27   Maruti Vitara Brezza LDi Option  2017         670000      70000  Diesel   
28                Fiat Palio 1.2 ELX  2003          70000      50000  Petrol   
29         Maruti Omni 8 Seater BSIV  2012         150000      35000  Petrol   
31  Maruti Alto 800 CNG LXI Optional  2019         330000      10000     CNG   
32        Maruti Alto K10 VXI Airbag  2019         366000      15000  Petrol   

   seller_type transmission         owner      mileage   engine max_power  \
22  Individual       Manual   First Owner    21.4 kmpl  1197 CC  83.1 bhp   
26  Individual       Manual   First Owner    16.8 kmpl   796 CC  34.2 bhp   
27  Individual       Manual   First Owner    24.3 kmpl  1248 CC  88.5 bhp   
28  Individual       Manual  Second Owner          NaN      NaN       NaN   
29  Individual       Manual  Second Owner    14.0 kmpl   796 CC    35 bhp   
31  Individual       Manual  Second Owner  33.44 km/kg   796 CC  40.3 bhp   
32  Individual       Manual   First Owner   23.95 kmpl   998 CC  67.1 bhp   

             torque  seats  
22   115Nm@ 4000rpm    5.0  
26    59Nm@ 2500rpm    8.0  
27   200Nm@ 1750rpm    5.0  
28              NaN    NaN  
29  6.1kgm@ 3000rpm    5.0  
31    60Nm@ 3500rpm    4.0  
32    90Nm@ 3500rpm    5.0

In [12]:
# Отображаем)
duplicates

name  year  selling_price  \
22                     Maruti Baleno Delta 1.2  2016         575000   
26                 Maruti Omni E MPI STD BS IV  2018         254999   
27             Maruti Vitara Brezza LDi Option  2017         670000   
28                          Fiat Palio 1.2 ELX  2003          70000   
29                   Maruti Omni 8 Seater BSIV  2012         150000   
...                                        ...   ...            ...   
6981  Ford Freestyle Titanium Plus Diesel BSIV  2018         750000   
6984  Ford Freestyle Titanium Plus Diesel BSIV  2018         746000   
6989                    Maruti Swift Dzire VDI  2015         625000   
6997                           Tata Indigo CR4  2013         290000   
6998                           Tata Indigo CR4  2013         290000   

      km_driven    fuel seller_type transmission         owner     mileage  \
22        45000  Petrol  Individual       Manual   First Owner   21.4 kmpl   
26        25000  Petrol  Individual       Manual   First Owner   16.8 kmpl   
27        70000  Diesel  Individual       Manual   First Owner   24.3 kmpl   
28        50000  Petrol  Individual       Manual  Second Owner         NaN   
29        35000  Petrol  Individual       Manual  Second Owner   14.0 kmpl   
...         ...     ...         ...          ...           ...         ...   
6981      24000  Diesel  Individual       Manual   First Owner   24.4 kmpl   
6984      24000  Diesel  Individual       Manual   First Owner   24.4 kmpl   
6989      50000  Diesel  Individual       Manual   First Owner  26.59 kmpl   
6997      25000  Diesel  Individual       Manual   First Owner  23.57 kmpl   
6998      25000  Diesel  Individual       Manual   First Owner  23.57 kmpl   

       engine  max_power               torque  seats  
22    1197 CC   83.1 bhp       115Nm@ 4000rpm    5.0  
26     796 CC   34.2 bhp        59Nm@ 2500rpm    8.0  
27    1248 CC   88.5 bhp       200Nm@ 1750rpm    5.0  
28        NaN        NaN                  NaN    NaN  
29     796 CC     35 bhp      6.1kgm@ 3000rpm    5.0  
...       ...        ...                  ...    ...  
6981  1498 CC  98.63 bhp  215Nm@ 1750-3000rpm    5.0  
6984  1498 CC  98.63 bhp  215Nm@ 1750-3000rpm    5.0  
6989  1248 CC     74 bhp       190Nm@ 2000rpm    5.0  
6997  1396 CC     70 bhp  140Nm@ 1800-3000rpm    5.0  
6998  1396 CC     70 bhp  140Nm@ 1800-3000rpm    5.0  

[1799 rows x 13 columns]

In [13]:
# Удаляем
df_train_clean = df_train.drop_duplicates(subset=feature_cols, keep='first')

In [14]:
# обновляем индексы
df_train = df_train_clean.reset_index(drop=True)

In [15]:
assert df_train.shape == (5840, 13)

### **Задание 4 (0.3 балла)**

Вы могли заметить, что с признаками ``mileage, engine, max_power и torque`` всё не очень хорошо. Они распознаются как строки (можно убедиться в этом, вызвав `data.dtypes`). Однако эти переменные не являются категориальными — они — числа. Соответственно, нужно привести их к числовому виду.

**Задача :**
* [ ] Уберите единицы измерения для признаков ``mileage, engine, max_power``.
* [ ] Приведите тип данных к ``float``.
* [ ] Предобработайте признак `torque` — разделите его на два: собственно `torque` и `max_torque_rpm`. Учтите единицы измерения


**Важно**
- Все действия нужно производить над обоими датасетами — `train` и `test`.

In [16]:
def get_num_from_str(series):
    series_updated = series.astype(str) \
      .str.extract(r'([0-9]*\.?[0-9]+)') \
      .astype(float)
    return series_updated

def split_str(series):
    torque_vals = []
    rpm_vals = []

    for x in series.astype(str):
        s = x.lower().replace(" ", "")
        s = s.replace("nm", "nm ")   # ставим пробел после Nm
        s = s.replace("@", " ")      # заменяем @ пробелом
        s = s.replace("at", " ")     # заменяем at пробелом

        parts = s.split()

        torque = re.findall(r"([0-9]*\.?[0-9]+)", parts[0])
        torque_vals.append(float(torque[0]) if torque else np.nan)

        rpm_candidates = re.findall(r"([0-9]+)rpm", s)
        rpm_vals.append(float(rpm_candidates[0]) if rpm_candidates else np.nan)

    return pd.Series(torque_vals), pd.Series(rpm_vals)



In [17]:
cols_to_clean = ['mileage', 'engine', 'max_power']
for col in cols_to_clean:
    df_train[col] = get_num_from_str(df_train[col])
    df_test[col] = get_num_from_str(df_test[col])


train_torque, train_rpm = split_str(df_train['torque'])
test_torque, test_rpm = split_str(df_test['torque'])

df_train['torque'] = train_torque
df_train['max_torque_rpm'] = train_rpm

df_test['torque'] = test_torque
df_test['max_torque_rpm'] = test_rpm


In [18]:
df_train.head()

name  year  selling_price  km_driven    fuel  \
0         Maruti Swift Dzire VDI  2014         450000     145500  Diesel   
1   Skoda Rapid 1.5 TDI Ambition  2014         370000     120000  Diesel   
2      Hyundai i20 Sportz Diesel  2010         225000     127000  Diesel   
3         Maruti Swift VXI BSIII  2007         130000     120000  Petrol   
4  Hyundai Xcent 1.2 VTVT E Plus  2017         440000      45000  Petrol   

  seller_type transmission         owner  mileage  engine  max_power  torque  \
0  Individual       Manual   First Owner    23.40  1248.0      74.00  190.00   
1  Individual       Manual  Second Owner    21.14  1498.0     103.52  250.00   
2  Individual       Manual   First Owner    23.00  1396.0      90.00   22.40   
3  Individual       Manual   First Owner    16.10  1298.0      88.20   11.50   
4  Individual       Manual   First Owner    20.14  1197.0      81.86  113.75   

   seats  max_torque_rpm  
0    5.0          2000.0  
1    5.0          2500.0  
2    5.0          2750.0  
3    5.0             NaN  
4    5.0          4000.0

In [19]:
df_train.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 5840 entries, 0 to 5839
Data columns (total 14 columns):
 #   Column          Non-Null Count  Dtype  
---  ------          --------------  -----  
 0   name            5840 non-null   object 
 1   year            5840 non-null   int64  
 2   selling_price   5840 non-null   int64  
 3   km_driven       5840 non-null   int64  
 4   fuel            5840 non-null   object 
 5   seller_type     5840 non-null   object 
 6   transmission    5840 non-null   object 
 7   owner           5840 non-null   object 
 8   mileage         5654 non-null   float64
 9   engine          5654 non-null   float64
 10  max_power       5656 non-null   float64
 11  torque          5653 non-null   float64
 12  seats           5654 non-null   float64
 13  max_torque_rpm  5315 non-null   float64
dtypes: float64(6), int64(3), object(5)
memory usage: 638.9+ KB


In [20]:
df_test.head()

name  year  selling_price  km_driven  \
0                  Mahindra Xylo E4 BS IV  2010         229999     168000   
1              Tata Nexon 1.5 Revotorq XE  2017         665000      25000   
2                    Honda Civic 1.8 S AT  2007         175000     218463   
3                    Honda City i DTEC VX  2015         635000     173000   
4  Tata Indica Vista Aura 1.2 Safire BSIV  2011         130000      70000   

     fuel seller_type transmission         owner  mileage  engine  max_power  \
0  Diesel  Individual       Manual   First Owner     14.0  2498.0      112.0   
1  Diesel  Individual       Manual   First Owner     21.5  1497.0      108.5   
2  Petrol  Individual    Automatic   First Owner     12.9  1799.0      130.0   
3  Diesel  Individual       Manual   First Owner     25.1  1498.0       98.6   
4  Petrol  Individual       Manual  Second Owner     16.5  1172.0       65.0   

   torque  seats  max_torque_rpm  
0   260.0    7.0          2200.0  
1   260.0    5.0          2750.0  
2   172.0    5.0          4300.0  
3   200.0    5.0          1750.0  
4    96.0    5.0          3000.0

In [21]:
df_test.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 1000 entries, 0 to 999
Data columns (total 14 columns):
 #   Column          Non-Null Count  Dtype  
---  ------          --------------  -----  
 0   name            1000 non-null   object 
 1   year            1000 non-null   int64  
 2   selling_price   1000 non-null   int64  
 3   km_driven       1000 non-null   int64  
 4   fuel            1000 non-null   object 
 5   seller_type     1000 non-null   object 
 6   transmission    1000 non-null   object 
 7   owner           1000 non-null   object 
 8   mileage         981 non-null    float64
 9   engine          981 non-null    float64
 10  max_power       981 non-null    float64
 11  torque          981 non-null    float64
 12  seats           981 non-null    float64
 13  max_torque_rpm  928 non-null    float64
dtypes: float64(6), int64(3), object(5)
memory usage: 109.5+ KB


**Выводы:**
В целом, некотоыр фичи можно хранить как int для оптимальности, например seats
Пример того, что нам нужно конвертнуть
- mileage	engine	max_power	torque
- 0	23.4 kmpl	1248 CC	74 bhp	190Nm@ 2000rpm
- 1	21.14 kmpl	1498 CC	103.52 bhp	250Nm@ 1500-2500rpm
- 2	23.0 kmpl	1396 CC	90 bhp	22.4 kgm at 1750-2750rpm
- 3	16.1 kmpl	1298 CC	88.2 bhp	11.5@ 4,500(kgm@ rpm)
- 4	20.14 kmpl	1197 CC	81.86 bhp	113.75nm@ 4000rpm

### **Задание 5 (0.3 балла)**

На первом шаге мы обнаружили пропуски. Давайте избавимся от них.

**Задание:**
- [ ] Заполните пропуски в столбцах медианами. Убедитесь, что после заполнения пропусков не осталось.
- [ ] Почему стоит применять именно медиану. Могли ли мы применить среднее? Обоснуйте свое рассуждение.
- [ ] Как правильно считать медиану для заполнения? Выберите верное утверждение:
 - По тестовым свою, по тренировочным — свою
 - По тренировочным данным для `train` и `test`






In [23]:
# Список колонок для заполнения
num_cols = ['mileage', 'engine', 'max_power', 'torque', 'max_torque_rpm', 'seats']

# Заполняем медианой только по train
for col in num_cols:
    median_train = df_train[col].median()
    df_train[col] = df_train[col].fillna(median_train)
    df_test[col] = df_test[col].fillna(median_train)  # медиана по train

# Проверяем, что пропусков нет
print(df_train[num_cols].isna().sum())
print("------------------------------")
print(df_test[num_cols].isna().sum())


mileage           0
engine            0
max_power         0
torque            0
max_torque_rpm    0
seats             0
dtype: int64
------------------------------
mileage           0
engine            0
max_power         0
torque            0
max_torque_rpm    0
seats             0
dtype: int64


**Выводы:**
Медиану стоит использовать потому что большая часть признаков асимметрично
Обычным средним можно заполнять, если нет выбросов. \
Тем не менее, можно испольщовать truncated mean усечененное среднее, или квантили. Но не будем усложнять \)0)) \

Касаемо того, на каком ДФе считать стату - на трейне. Мы не видим тест и в стату, которой мы будем заполнять пропуски не должны попадать обьекты из будущего. Это же касается кат фичей. Если энкодим что-то, то должны это делать на трейне, вне зависимсоти от того, что может какой-то новый класс прилететь к нам в тесте (или на инференсе)

### **Задание 6 (0.2 балла)**

Теперь, когда не осталось пропусков, давайте преобразуем столбцы к более подходящим типам. А именно столбцы ``engnine`` и ``seats`` к приведем к `int`.

- [ ] Осуществите приведение столбцов к необходимому типу.
- [ ] Ответье на вопрос — почему (хоть мы этого и не делаем) ``seats``, возможно рассмотреть как категориальную переменную?

In [24]:
# Приведение к int
df_train['engine'] = df_train['engine'].astype(int)
df_test['engine'] = df_test['engine'].astype(int)

df_train['seats'] = df_train['seats'].astype(int)
df_test['seats'] = df_test['seats'].astype(int)

# Проверим типы
print(df_train[['engine', 'seats']].dtypes)
print(df_test[['engine', 'seats']].dtypes)


engine    int64
seats     int64
dtype: object
engine    int64
seats     int64
dtype: object


- Seats - можно кодировать, как кат фичу. Тем не менее, это не стоит делать, конкретно в линейной модели. Есть момент экстрополяции. Лин рег хорошо экстрополирует, и в случае если каким то образом у нас в тесте появится машина с 100500 местами, то модель свяжет с таргетом и будет какое-то линейное предсказание. Если мы закодируем в кат фичу эту колонку, может получиться что-то не очень понятное. Но нужно эксперементировать. \
В деревяшках такой эффект наверное особо и не будет наблюдаться.
- engine - тож можем, разбить на интервальчики, например по квантили. Типа [1, 100], [101, 200] и тд. И каждый интервел кодировать


### **Задание 7 (0.1 балла)**

Снова вызовите метод describe и проанализируйте статистики.

**Ответье на вопрос:**
- [ ] Есть ли основания предполагать, что заполнение пропусков свдинуло наши распределения? Могло ли это вообще возникнуть?

In [25]:
df_train_clean.describe()

year  selling_price     km_driven       seats
count  5840.000000   5.840000e+03  5.840000e+03  5654.00000
mean   2013.428425   5.229601e+05  7.395224e+04     5.44075
std       4.095622   5.354320e+05  6.007114e+04     0.99527
min    1983.000000   2.999900e+04  1.000000e+00     2.00000
25%    2011.000000   2.500000e+05  3.900000e+04     5.00000
50%    2014.000000   4.050000e+05  7.000000e+04     5.00000
75%    2017.000000   6.400000e+05  1.000000e+05     5.00000
max    2020.000000   1.000000e+07  2.360457e+06    14.00000

In [26]:
df_train.describe()

year  selling_price     km_driven      mileage       engine  \
count  5840.000000   5.840000e+03  5.840000e+03  5840.000000  5840.000000   
mean   2013.428425   5.229601e+05  7.395224e+04    19.430841  1429.448973   
std       4.095622   5.354320e+05  6.007114e+04     3.985973   485.662834   
min    1983.000000   2.999900e+04  1.000000e+00     0.000000   624.000000   
25%    2011.000000   2.500000e+05  3.900000e+04    16.950000  1197.000000   
50%    2014.000000   4.050000e+05  7.000000e+04    19.370000  1248.000000   
75%    2017.000000   6.400000e+05  1.000000e+05    22.300000  1498.000000   
max    2020.000000   1.000000e+07  2.360457e+06    42.000000  3604.000000   

         max_power       torque        seats  max_torque_rpm  
count  5840.000000  5840.000000  5840.000000     5840.000000  
mean     87.906371   161.309570     5.426712     3022.227397  
std      31.640418    91.174286     0.982344      883.703006  
min       0.000000     4.800000     2.000000        0.000000  
25%      68.000000    99.040000     5.000000     2400.000000  
50%      81.860000   150.000000     5.000000     3000.000000  
75%      99.000000   200.000000     5.000000     3750.000000  
max     400.000000   789.000000    14.000000     5300.000000

**Выводы:**
Вообщем - нет. У нас не оч много прпоусков.
В большинстве случаев — нет, если пропусков немного. Мы используем медиану, что бы как раз не скашивать распределение сильно

В теории, это может быть:
- Если например у нас у каких-то не случайных страт отсутствовали значения каких-либо признаков. Например, transmission=Manual много пропусков в каких-либо числ фичах. В таких случаях заполнение медианой сместит распределение в сторону средней машины.

## **Визуализации и корреляция (1.6 балла + 0.25)**

Визуализация данных — важный шаг в работе. Визуализировать данные необходимо, например, чтобы:

- Оценить распределения признаков самих по себе (это может натоклнуть вас на мысли о модели, которую можно использовать)
- Сравнить распределения на `train` и `test` — чтобы проверить, насколько информация, на которой вы будете обучаться согласуется с той, на которой модель должна работать
- Оценить есть ли явная связь признаков с целевой переменной

**Важно:**

Если распределения на `train` и `test` не совпадают, это не значит, что нужно перемешивать данные! Более корректно актуализировать задачу и уточнить, а не устарели ли данные `train`. Также полезным может быть собрать новую тестовую выборку, смешав те, что имеются сейчас.

**Если вы будете подгонять распределения, то можете встретиться с переобучением!**

### **Задание 8 (0.5 балла)**

Шаг 1.
- [ ] Воспользуйтесь `pairplot` из библиотеки `seabron`, чтобы визуализировать попарные распределения числовых признаков для `train`
- [ ] По полученному графику ответьте на вопросы:
 - Можно ли предположить на основе распределений связь признаков с целевой переменной?
 - Можно ли предположить на основе распределений выдвинуть гипотезу о корреляциях признаков?

Шаг 2.

- [ ] Постройте pairplot по тестовым данным
- [ ] Ответьте на вопрос "Похожими ли оказались совокупности при разделении на трейн и тест?"

In [27]:
# Числовые признаки
num_cols = ['year', 'km_driven', 'seats', 'mileage', 'engine', 'max_power', 'torque', 'max_torque_rpm', 'selling_price']

# Ограничим количество точек для удобства
sns.pairplot(df_train[num_cols], diag_kind='kde')
plt.show()

In [28]:
sns.pairplot(df_test[num_cols], diag_kind='kde')
plt.show()

**Выводы:** \
С таргетм:
- На цену автомобиля больше всего влияют: max_power, torque, engine и year (что в целом очень логично)
- km_driven и mileage тоже влияют, но слабее (пробег скорее всего тоже супер важная фича, но она нелинейно коррелирует)

Попарные между собой:
- Признаки мощности и объёма двигателя тесно связаны между собой, что логично: более мощные машины обычно имеют больший двигатель и крутящий момент.
- mileage обратно коррелирует с мощностью и размером автомобиля — большие мощные машины менее экономичны.


Корреляции очень похожи между train и test:
1) Направления корр-ий очень похожи. Значит, train и test — однородные выборки, распределения признаков схожи.
2) max_power, torque, engine и year — ключевые признаки для предсказания цены.
3) km_driven и mileage — слабые, но полезные признаки. (производные их могут выстрелить)
4) Между признаками мощности (max_power, torque, engine) сильная корреляция — это нужно учитывать в линейных моделях, риск частичной мультиколлиниарности и дальнейшей плохой обусловленности матрицы Грамма

Train и test очень похожи, можно пробовать обучать бейзлайн даже на этом

### **Задание 9 (0.5 балла)**

И так, вы выдвинули гипотезы о наличии связи. Теперь давайте оценим эту связь в числах.

**Задание:**
- [ ] Получите значения коэффициента корреляции Пирсона для тренировочного набора данных при помощи `pd.corr()`
- [ ] По полученным корреляциям постройте тепловую карту (`heatmap` из бибилотеки seaborn)

In [29]:
# Корреляционная матрица
corr_train = df_train[num_cols].corr(method='pearson')

plt.figure(figsize=(10,8))
sns.heatmap(corr_train, annot=True, fmt=".2f", cmap='coolwarm', square=True)
plt.title("Correlation Heatmap (Train)")
plt.show()


In [30]:
# Корреляционная матрица с методом Спирмена
corr_train = df_train[num_cols].corr(method='spearman')

plt.figure(figsize=(10,8))
sns.heatmap(corr_train, annot=True, fmt=".2f", cmap='coolwarm', square=True)
plt.title("Correlation Heatmap (Train)")
plt.show()


- [ ] Ответьте на вопросы:
 - Какие 2 признака наименее скоррелированы между собой?
 - Между какими наблюдается довольно сильная положительная линейная зависимость?
 - Правильно ли, опираясь на данные, утверждать, что чем меньше год, тем, скорее всего, больше километров проехала машина к дате продажи?
 - Изучите типы корреляций в `pd.corr()`. Какую вы использовали по умолчанию?

`Your answer here`
- По таблице корреляций самые близкие к 0 значения: \
  - max_power и max_torque_rpm
  - engine и year

- Наиболее высокие положительные корреляции: \
  - max_power и torque
  - engine и torque
  - engine и max_power
Писал выше, что тут большой риск частичной мультиколлиниарности

- Корреляция year и km_driven ≈ -0.37 \
Вывод:
Действительно, чем меньше год выпуска, тем больше вероятность, что автомобиль проехал больше километров. Логично объяснима: старые автомобили в среднем имеют больший пробег. О следствии мы тут не говорим

- Использовал по умолчанию, но так же посмотрел Спирмена

### **Задание 10 (0.6 балла)**

По умолчанию `pd.corr` возвращает корреляцию Пирсона, говорящую о линейной взаимосвязи. Но зависимости существуют не только линейные! В этой задаче, попробуйте измерить другие способы вычисления корреляций.

- [ ] Реализуйте корреляцию Спирмена/Кендала (на выбор) без использования библиотек (можно пользоваться только `numpy`). Сравните результаты вычисления с библиотечной реализацией
- [ ] Сделайте выводы


Постройте матрицу корреляции [phik](https://pypi.org/project/phik/)
- [ ] Проинтерпретируйте результаты


In [31]:
def spearman_corr(df):
    """
    Корреляция Спирмена
    """
    numeric_df = df.select_dtypes(include=[np.number]).copy()
    cols = numeric_df.columns
    n = len(cols)

    # Ранжируем значения
    ranks = numeric_df.rank(axis=0, method='average').values  # ранги с учётом среднего при равных значениях

    # Матрица корреляций
    corr_matrix = np.zeros((n, n))

    for i in range(n):
        for j in range(n):
            x = ranks[:, i]
            y = ranks[:, j]
            corr_matrix[i, j] = np.corrcoef(x, y)[0, 1]

    return pd.DataFrame(corr_matrix, index=cols, columns=cols)

In [32]:
spearman_corr_train = spearman_corr(df_train[num_cols])

plt.figure(figsize=(10,8))
sns.heatmap(spearman_corr_train, annot=True, fmt=".2f", cmap='coolwarm', square=True)
plt.title("Correlation Heatmap (Train)")
plt.show()

In [33]:
cols = df_train.columns
phik_corr = df_train[cols].phik_matrix(interval_cols=num_cols)

plt.figure(figsize=(12,10))
sns.heatmap(phik_corr, annot=True, fmt=".2f", cmap="coolwarm", square=True)
plt.title("Phik матрица")
plt.show()


`Your answer here` \
**Выводы:**
- Библиотечный варинат варианта Спримена и from scratch схожи. Особо нечего сказать\)))

- Phik учитывает любые типы зависимостей, включая нелинейные и категориальные.
- В отличие от Pearson, который показывает только линейную связь, Phik может выявлять скрытые зависимости между признаками. Можно юзать дял смешанных типов фичей
- name — самый сильный регрессор из всех признаков, поскольку модель автомобиля фиксирует большинство характеристик в строке
- Сильная зависимость между характеристиками (engine, max_power, torque, mileage)
- Цена сильно зависит от мощности и характеристик, но напрямую почти не зависит от пробега
- Прзнаки fuel, transmission, seller_type, owner оказывают не самое сильное влияние на цену
- km_driven почти не зависит от остальных признаков — возможно, пробег равномерно распределён по моделям

### **Дополнительные визуализации (бонус 0.25 балла)**

Если вам кажется, что мы не попросили вас нарисовать какие-то очень важные зависимости, нарисуйте их и поясните.
Один график: 0.125 балла, при условии, что он обоснован.

In [35]:
plt.figure(figsize=(16,6))

# График 1: Selling Price vs Max Power
plt.subplot(1, 2, 1)
sns.scatterplot(
    data=df_train,
    x='max_power',
    y='selling_price',
    hue='engine',
    palette='viridis',
    alpha=0.7
)
plt.title('Цена vs Power')
plt.xlabel('Power (bhp)')
plt.ylabel('Selling Price ($)')
plt.yscale('log') # логарифм берем, так как в цене есть выбросы, не оч приятно визуально смотреть на такие графики, но лог-е не повиляет на визуальную интуицию
plt.legend(title='Engine (CC)', bbox_to_anchor=(1.05, 1), loc='upper left')

# График 2: Selling Price vs Torque
plt.subplot(1, 2, 2)
sns.scatterplot(
    data=df_train,
    x='torque',
    y='selling_price',
    hue='engine',
    palette='plasma',
    alpha=0.7
)
plt.title('Цена vs Torque')
plt.xlabel('Torque (Nm)')
plt.ylabel('Selling Price')
plt.yscale('log')
plt.legend(title='Engine (CC)', bbox_to_anchor=(1.05, 1), loc='upper left')

plt.tight_layout()
plt.show()


In [39]:
sns.boxplot(data=df_train, x='fuel', y='selling_price', palette='Set1')
plt.title('Цена по типу топлива')
plt.show()

In [40]:
sns.boxenplot(data=df_train, x='seller_type', y='selling_price', palette='Set1')
plt.title('Цена по виду продавца')
plt.show()

**Выводы:**
Обоснование выбора:
- Phik показал сильную связь между selling_price и признаками двигателя: max_power (0.872), torque (0.752) и engine (0.504).

- Max Power и Selling Price
  - Цена растёт с увеличением мощности двигателя
  - Для одинаковой мощности цена выше у автомобилей с большим объёмом двигателя

- Torque и Selling Price
  - Аналогично, чем выше крутящий момент, тем выше цена
  - Также наблюдается влияние engine: для одинакового крутящего момента цена выше у автомобилей с большим двигателем


Вывод:
- Кажется, что мощность и крутящий момент двигателя — ключевые признаки, определяющие цену автомобиля. Предположительно, даже на таком наборе признаков можно получить хороший бейзлайн

# **Часть 2 (1.7 балла) | Модель только на вещественных признаках**

В этой части вам предстоит обучить модель только на вещественных признаках. Почему только на них?

Чем больше признаковое пространство — чем сложнее модель. А чем модель проще — тем лучше для скорости работы и интерпретации признаков.

За задания этой части вы можете набрать 1.7 основных и 0.15 бонусных балла;

### **Задание 11 (0.05 балла)**

Сделайте на тренировочный и тестовый наборы. Она уже даны, достаточно просто отделить целевой признак. Перед разбиением создайте копию датафрейма, который будет хранить только вещественные признаки и используйте его (то есть категориальные столбцы (все, кроме seats) необходимо удалить).

В переменные y_train и y_test запишите значения целевых переменных. Используйте уже имеющиеся данные train и test. Если считаете уместным применить какую-то более хитрую технику разбиения — примените, но опишите, зачем.

In [41]:
X_train_nums = df_train[num_cols].drop("selling_price", axis=1)
X_test_nums = df_test[num_cols].drop("selling_price", axis=1)

In [42]:
y_train = df_train["selling_price"]
X_train = X_train_nums

In [43]:
X_train.describe()

year     km_driven        seats      mileage       engine  \
count  5840.000000  5.840000e+03  5840.000000  5840.000000  5840.000000   
mean   2013.428425  7.395224e+04     5.426712    19.430841  1429.448973   
std       4.095622  6.007114e+04     0.982344     3.985973   485.662834   
min    1983.000000  1.000000e+00     2.000000     0.000000   624.000000   
25%    2011.000000  3.900000e+04     5.000000    16.950000  1197.000000   
50%    2014.000000  7.000000e+04     5.000000    19.370000  1248.000000   
75%    2017.000000  1.000000e+05     5.000000    22.300000  1498.000000   
max    2020.000000  2.360457e+06    14.000000    42.000000  3604.000000   

         max_power       torque  max_torque_rpm  
count  5840.000000  5840.000000     5840.000000  
mean     87.906371   161.309570     3022.227397  
std      31.640418    91.174286      883.703006  
min       0.000000     4.800000        0.000000  
25%      68.000000    99.040000     2400.000000  
50%      81.860000   150.000000     3000.000000  
75%      99.000000   200.000000     3750.000000  
max     400.000000   789.000000     5300.000000

In [44]:
y_test = df_test["selling_price"]
X_test = X_test_nums

### **Задание 12. (0.2 балла)**

Построим нашу первую модель!
- [ ] Обучите классическую линейную регрессию с дефолтными параметрами. Посчтитайте $R^2$ и $MSE$ для трейна и для теста.
- [ ] Сделайте выводы по значениям метрик качества.

**Примечание:**

Здесь и далее $R^2$ и $MSE$ для трейна и для теста выводите везде, где требуется обучать модели, даже если в явном виде этого не просят. Иначе непонятно, как понять, насколько успешны наши эксперименты.

In [45]:
model_nums = LinearRegression()
model_nums.fit(X_train, y_train)

model_nums_train_pred = model_nums.predict(X_train)
model_nums_test_pred = model_nums.predict(X_test)

In [55]:
# Напишем вспом функцию

def get_metrics(y_train_true, y_train_pred, y_test_true, y_test_pred):
    """
    Принт метрик
    """
    print(f"R2 для трейна: {r2_score(y_train_true, y_train_pred)}")
    print(f"R2 для теста: {r2_score(y_test_true, y_test_pred)}")
    print(f"MSE для трейна: {MSE(y_train_true, y_train_pred)}")
    print(f"MSE для теста: {MSE(y_test_true, y_test_pred)}")


get_metrics(y_train, model_nums_train_pred, y_test, model_nums_test_pred)

R2 для трейна: 0.6022667915986439
R2 для теста: 0.6010938010055462
MSE для трейна: 114005585965.91573
MSE для теста: 229302674203.2037


**Вывод:**
- Р^2 схожий почти
- MSE - на тесте выше, это нам не говорит про переообучени или недообучение. Может быть связанно с масштабом таргета (очень дорогие автомобили)
- Базовая линейная регрессия даёт не самый высокий результат.
- Значительная часть дисперсии цены всё ещё не объяснена, что может говорить о нелинейных зависимостей и взаимодействий признаков, которые линейная модель не улавливает.



### **Задание 13 (0.15 балла)**

- [ ] Реализуйте $R^2$ руками. Приведите формулу $R^2$ и объясните каждую компоненту метрики

In [47]:
def MSE_scratch(y_true, y_pred):
  return 1/len(y_train) * np.sum(np.power(y_train - model_nums_train_pred, 2))

def r2_scratche(y_true, y_pred):
    ss_res = np.sum((y_true - y_pred)**2)
    ss_tot = np.sum((y_true - np.mean(y_true))**2)
    r2 = 1 - ss_res / ss_tot
    return r2

r2_train_scratche = r2_scratche(y_train, model_nums_train_pred)
r2_test_scratche = r2_scratche(y_test, model_nums_test_pred)

print(f"R2 трейн: {r2_train_scratche}")
print(f"R2 тест: {r2_test_scratche}")

R2 трейн: 0.6022667915986439
R2 тест: 0.6010938010055462


**Вывод** \
  ss_res = np.sum((y_true - y_pred)**2) # сколько вариации модель не обьяснила \
  ss_tot = np.sum((y_true - np.mean(y_true))**2) # сколько всего вариации есть в данных \

Результат схож с библиотечной реализацией

### **Бонус (0.15 балла)**

- [ ] Реализуйте [$\text{adjusted}-R^2$](https://en.wikipedia.org/wiki/Coefficient_of_determination).
- [ ] Объясните, когда применяется $\text{adjusted}-R^2$?

In [48]:
def r2_adjusted_scratch(y_true, y_pred, n_features):
    n = len(y_true)
    r2 = r2_scratche(y_true, y_pred)
    r2_adj = 1 - (1 - r2) * (n - 1) / (n - n_features - 1)
    return r2_adj

n_features = X_train.shape[1]

r2_adj_train = r2_adjusted_scratch(y_train, model_nums_train_pred, n_features)
r2_adj_test = r2_adjusted_scratch(y_test, model_nums_test_pred, n_features)

print(f"Adjusted R2_train: {r2_adj_train:.4f}")
print(f"Adjusted R2_test:  {r2_adj_test:.4f}")

Adjusted R2_train: 0.6017
Adjusted R2_test:  0.5979


Можно использовать в случае, если мы хотим uplift посмотреть от добавлении новых фичей, а так же, если хотим сравнить модели одного и того же семейства, но с разными признаками (фиксируя гип-ы например)

### **Задание 14 (0.05 балла)**

Всегда есть место совершенству. Поэтому давайте попробуем улучшить модель. При помощи стандартизации признаков.

- [ ] Стандартизируйте значения в тренировочных и тестовых данных. Стандартизатор **обучайте только на `train`**.

In [56]:
scaler = StandardScaler()

# Обучаем только на тренировочных данных
X_train_scaled = scaler.fit_transform(X_train)
X_test_scaled = scaler.transform(X_test)

model_nums_scaled = LinearRegression()
model_nums_scaled.fit(X_train_scaled, y_train)

model_nums_scaled_train_pred = model_nums_scaled.predict(X_train_scaled)
model_nums_scaled_test_pred = model_nums_scaled.predict(X_test_scaled)

# Метрики со скейлером
get_metrics(y_train, model_nums_scaled_train_pred, y_test, model_nums_scaled_test_pred)

R2 для трейна: 0.6022667915986439
R2 для теста: 0.6010938010055561
MSE для трейна: 114005585965.91573
MSE для теста: 229302674203.19806


### **Задание 15 (0.1 балла)**

Хотя стандартизация не помогла сильно прибавить в качестве она открыла возможность интерпретировать важность признаков в модели. Правило интерпретации такое:

Чем больше коэффициент $\beta_i$ по модулю, тем важнее признак.

**Ответьте на вопрос:**

- [ ] Какой признак оказался наиболее информативным в предсказании цены?

In [57]:
coef_df = pd.DataFrame({
    'feature': X_train.columns,
    'coefficient': np.abs(model_nums_scaled.coef_)
})

coef_df = coef_df.sort_values(by='coefficient', ascending=False)
coef_df[['feature', 'coefficient']]

feature    coefficient
5       max_power  301227.720151
0            year  160292.954525
1       km_driven   48228.798690
6          torque   44953.619848
7  max_torque_rpm   43356.459270
2           seats   32796.941606
4          engine   22692.889616
3         mileage   10349.930086

**Вывод:**
Самыми важными признаками оказались: мощность двигателя и год машины
- max_power
- year

### **Задание 16 (0.25 балла)**

Попробуем улучшить нашу модель с помощью применения регуляризации. Для этого воспльзуемся `Lasso` регрессией.  Кроме того, попробуйте использовать её теоретическое свойство отбора признаков, за счет зануления незначимых коэффициентов.

**Задание:**

- [ ] Обучите Lasso регрессию на тренировочном наборе данных с нормализованными признаками. Оцените её качество
- [ ] Проверьте, занулила ли L1-регуляризация с параметрами по умолчанию какие-нибудь веса? Предположите почему.

In [58]:
model_nums_scaled_lasso = Lasso()
model_nums_scaled_lasso.fit(X_train_scaled, y_train)

model_nums_scaled_lasso_train_pred = model_nums_scaled_lasso.predict(X_train_scaled)
model_nums_scaled_lasso_test_pred = model_nums_scaled_lasso.predict(X_test_scaled)

get_metrics(y_train, model_nums_scaled_lasso_train_pred, y_test, model_nums_scaled_lasso_test_pred)

R2 для трейна: 0.6022667915507067
R2 для теста: 0.6010925546718202
MSE для трейна: 114005585979.65634
MSE для теста: 229303390631.4193


In [59]:
model_nums_scaled_lasso.coef_

array([160290.63746956, -48227.87528386, -32793.03106414, -10346.54878359,
        22690.91992119, 301228.65358184,  44953.76320126, -43354.13198497])

In [60]:
model_nums_scaled.coef_

array([160292.95452496, -48228.79869009, -32796.9416056 , -10349.93008586,
        22692.88961627, 301227.72015144,  44953.61984823, -43356.45927039])

**Вывод:**
- Все признаки важны, все признаки нужны
- L1-штраф слабый из-за скейлинга. Масштаб таргета и фичей становится несоизмеримым

### **Задание 17. Финальный рывок (0.4 балла)**

До этого мы с вами использовали `train` для обучения и `test` для прогнозирования. Но у нас есть ещё одна задача — подобрать оптимальные параметры модели. Для этого используем кросс-валидацию, описанную на семинарах.

Кроме того, выжмем максимум из модификаций регрессии. Построим `ElasticNet`. И сделаем всё по порядку.

**Ваша задача 1:**

- [ ] Перебором по сетке (c 10-ю фолдами) подберите оптимальные параметры для Lasso-регрессии. Вам пригодится класс [GridSearchCV](https://scikit-learn.org/stable/modules/generated/sklearn.model_selection.GridSearchCV.html).
- [ ] Ответьте на вопросы:
 - Сколько грид-сёрчу пришлось обучать моделей?
 - Что значит каждый параметр `param_grid`, который вы заполняли для `GridSearch`? Опишите каждый
 - Какой коэффициент регуляризации у лучшей из перебранных моделей? Занулились ли какие-нибудь из весов при такой регуляризации?

In [62]:
param_grid = {
    'alpha': [0.1, 0.2, 0.5, 1, 2, 5, 10, 20, 50, 100, 200, 500, 1000, 2000, 5000, 10000],
    'max_iter': [1000, 5000, 10000, 20000, 50000, 100000],
    'tol': [1e-6, 1e-5, 1e-4, 1e-3, 1e-2]
}

lasso = Lasso()
grid = GridSearchCV(
    estimator=lasso,
    param_grid=param_grid,
    cv=10,
    scoring="neg_mean_squared_error",
    n_jobs=-1
)

print('best params:')
grid.fit(X_train_scaled, y_train)
print(grid.best_params_)

print('----------------------------')

model_nums_scaled_lasso_optimal = Lasso(**grid.best_params_)
model_nums_scaled_lasso_optimal.fit(X_train_scaled, y_train)

model_nums_scaled_lasso_optimal_train_pred = model_nums_scaled_lasso_optimal.predict(X_train_scaled)
model_nums_scaled_lasso_optimal_test_pred = model_nums_scaled_lasso_optimal.predict(X_test_scaled)

get_metrics(y_train, model_nums_scaled_lasso_optimal_train_pred, y_test, model_nums_scaled_lasso_optimal_test_pred)

best params:
{'alpha': 5000, 'max_iter': 1000, 'tol': 0.01}
----------------------------
R2 для трейна: 0.6015320264016439
R2 для теста: 0.5951088383831465
MSE для трейна: 114216197841.06697
MSE для теста: 232743001622.98782


- 3 сек
- Коэффы:
  - alpha — коэффициент L1-регуляризации
  - max_iter — максимальное число итераций оптимизации
  - tol — критерий остановки
- alpha=100
- не занулились

**Ваша задача 2:**

- [ ] Перебором по сетке (c 10-ю фолдами) подберите оптимальные параметры для [ElasticNet](https://scikit-learn.org/stable/modules/generated/sklearn.linear_model.ElasticNet.html) регрессии.
- [ ] Ответьте на вопрос:
 - Сколько грид-сёрчу пришлось обучать моделей?
 - Какие гиперпараметры соответствуют лучшей (по выбранной метрике качества) из перебранных моделей?

In [63]:
param_grid = {
    'alpha': [0.0001, 0.001, 0.005, 0.01, 0.02, 0.05, 0.1, 0.5, 1, 2, 5],
    'l1_ratio': list(float(round(i,1)) for i in np.arange(0.1, 1, 0.1)),
}

grid = GridSearchCV(
    estimator=ElasticNet(),
    param_grid=param_grid,
    cv=10,
    scoring='neg_mean_squared_error'
)

print('best params:')
grid.fit(X_train_scaled, y_train)
print(grid.best_params_)

print('----------------------------')

model_nums_scaled_ElasticNet_optimal = ElasticNet(**grid.best_params_)
model_nums_scaled_ElasticNet_optimal.fit(X_train_scaled, y_train)

model_nums_scaled_ElasticNet_optimal_train_pred = model_nums_scaled_ElasticNet_optimal.predict(X_train_scaled)
model_nums_scaled_ElasticNet_optimal_test_pred = model_nums_scaled_ElasticNet_optimal.predict(X_test_scaled)

get_metrics(y_train, model_nums_scaled_ElasticNet_optimal_train_pred, y_test, model_nums_scaled_ElasticNet_optimal_test_pred)

best params:
{'alpha': 0.02, 'l1_ratio': 0.4}
----------------------------
R2 для трейна: 0.6021287054279871
R2 для теста: 0.5986545937470279
MSE для трейна: 114045166756.42299
MSE для теста: 230704800188.52063


**Вывод**
- 1 сек
- {'alpha': 0.02, 'l1_ratio': 0.4}

### **Задание 18 (0.35 балла)**

И так, вы обучили все варианты регуляризаций, доступные в sklearn, но не все, что мы обсудили на занятии! И следующее задание о забытой - $L0$ регуляризации.


**Ваша задача:**>
- [ ] Реализуйте модель с $L0$-регуляризаицей.
- [ ] Обучите модель на данных и проанализируйте результат, экспериментируя с коэффициенитом регуляризации
- [ ] Проанализируйте результаты обучения

**Важно:**

Вопреки тому, что L0 не реализована в стандартных пакетах, концепция данной регуляризации не является мертвой. Она может встречаться в [статьях](https://arxiv.org/abs/1712.01312) и экспериментах.



In [264]:
import numpy as np
from scipy.optimize import minimize


def l0_regularized_regression(X, y, lambda_, epsilon=1e-3, max_iter=100):

    n_samples, n_features = X.shape

    # Сначала находим обычные коэффициенты линейной регрессии (без регуляризации)
    beta = np.linalg.lstsq(X, y, rcond=None)[0]

    # функция аппроксимации l0 нормы
    def l0_approx(beta):
        return np.sum(1 - np.exp(-beta**2 / (2 * epsilon**2)))

    def objective(beta):
        # Вычисляем ошибку
        y_pred = X @ beta
        mse = np.mean((y - y_pred) ** 2)
        l0_approx_value = l0_approx(beta)

        # Полная целевая функция (||y_true - y_pred||^2 + lambda * ||w||_0)
        return mse + l0_approx_value * lambda_

    # Оптимизация
    bounds = [(-10, 10) for _ in range(n_features)]
    result = minimize(
        objective,
        beta,
        method='L-BFGS-B',
        bounds=bounds,
        options={'maxiter': max_iter, 'disp': True}
    )

    return result.x

In [265]:
# Пример использования
beta_l0 = l0_regularized_regression(X_train_scaled, y_train, lambda_=0.1)
print("Коэффициенты:", beta_l0)
print("Ненулевые коэффициенты:", np.sum(np.abs(beta_l0) > 1e-6))

Коэффициенты: [ 10. -10.  10. -10.  10.  10.  10. -10.]
Ненулевые коэффициенты: 8


/tmp/ipython-input-3802943733.py:29: DeprecationWarning: scipy.optimize: The `disp` and `iprint` options of the L-BFGS-B solver are deprecated and will be removed in SciPy 1.18.0.
  result = minimize(


In [266]:
for lam in [0, 1, 3, 7, 10]:
    s = l0_regularized_regression(X_train_scaled, y_train, lam)
    print(f"lambda = {lam}: выбрано признаков — {len(s)}")


lambda = 0: выбрано признаков — 8
lambda = 1: выбрано признаков — 8
lambda = 3: выбрано признаков — 8
lambda = 7: выбрано признаков — 8
lambda = 10: выбрано признаков — 8


/tmp/ipython-input-3802943733.py:29: DeprecationWarning: scipy.optimize: The `disp` and `iprint` options of the L-BFGS-B solver are deprecated and will be removed in SciPy 1.18.0.
  result = minimize(


**Вывож:**
- У задача с l0 рег-ией не существует closed-form решения. Есть несколько способов аппроксимации
- Эффект, что l0 в нашем случае может не работаь, потому что все признаки могуть быть важны

# **Часть 3 (0.5 балла) | Добавляем категориальные фичи**

Попробуем для улучшения модели дать ей больше признаков. Добавим категориальные фичи.

За эту часть можно набрать 0.5 основных балла.



### **Задание 19 (0.1 балла)**

Проанализируйте столбец `name`. Очевидно, что эта переменная является категориальной, однако категорий в ней много.

- [ ] Предобработайте столбец `name`, чтобы избежать его удаления

In [64]:
X_train_nums.shape

(5840, 8)

In [65]:
X_train_cat = df_train.drop("selling_price", axis=1)
X_test_cat = df_test.drop("selling_price", axis=1)

In [66]:
X_train_cat.shape, X_test_cat.shape

((5840, 13), (1000, 13))

In [67]:
# Выделяем бренд
X_train_cat['name'] = X_train_cat['name'].str.split().str[0]
X_test_cat['name'] = X_test_cat['name'].str.split().str[0]

# Проверим уникальные значения
print(X_train_cat['name'].nunique())

30


In [68]:
# WTF? 5 кат фичей же
assert X_train_cat.shape == (5840, 11)

AssertionError: 

### **Задание 20 (0.1 балла)**

- [ ] Закодируйте категориалльные фичи и ``seats`` методом OneHot-кодирования.

In [69]:
# Список категориальных признаков
categorical_cols = ['fuel', 'seller_type', 'transmission', 'owner', 'name', 'seats']

# Объединяем train и test, чтобы учесть все категории
df_all = pd.concat([X_train_cat, X_test_cat], axis=0, sort=False)

# One-Hot кодирование с пандасом с удалением первого столбца каждой категории
df_all_encoded = pd.get_dummies(df_all, columns=categorical_cols, drop_first=True)

X_train_cat = df_all_encoded.iloc[:len(X_train_cat), :].copy()
X_test_cat = df_all_encoded.iloc[len(X_train_cat):, :].copy()

print(X_train_cat.shape, X_test_cat.shape)


(5840, 56) (1000, 56)


### **Задание 21 (0.2 балла)**

OHE — базовый алгоритм преобразования категориальных признаков, но и с ним нужно быть аккуратными.

**Ответьте на вопросы:**


* Как корректно работать с OHE преобразованием?
* Почему мы удаляем один столбец?
* Пусть из $n$ признаков мы получили $n-1$ столбец, из которых $k < n -1$ оказались не важными по весам модели. Корректно ли их удалить?

**ОТВЕТ**
- Нужно обьеденяиь train и test перед кодированием, чтобы учесть все категории. Надо недопустить, что бы в тесте были категории, которых нет в трейне.

- Почему удаляем один столбец?
Чтобы избежать линейной зависимости между бинарными столбцами. Это предотвращает проблемы при обучении линейных моделей.

- Да, если коэффициенты близки к нулю, их можно удалить для уменьшения размерности.


### **Задание 22 (0.1 балла)**
Повторим то, что делали на прошлом шаге для моделей на вещественных признаках, однако теперь с моделью `Ridge`.


**Ваша задача:**
- [ ] Переберите параметр регуляризации `alpha` для гребневой (ridge) регрессии с помощью класса `GridSearchCV` В качестве параметров при объявлении GridSearchCV кроме модели укажите метрику качества $R^2$. Кроссвалидируйтесь по 10-ти фолдам.
- [ ] Ответье на вопрос: Удалось ли улучшить качество прогнозов?

In [72]:
scaler = StandardScaler()
X_train_cat_scaled = scaler.fit_transform(X_train_cat)
X_test_cat_scaled = scaler.transform(X_test_cat)

# Параметры для перебора

param_grid = {
    'alpha': [0.1, 0.2, 0.5, 1, 2, 5, 10, 20, 50, 100, 200, 500, 1000, 2000, 5000, 10000]
}

grid_search = GridSearchCV(
    estimator=Ridge(),
    param_grid=param_grid,
    cv=10,
    scoring='r2',
)

print('best params:')
grid_search.fit(X_train_scaled, y_train)
print(grid_search.best_params_)

ridge_cat_sc_gs = Ridge(**grid_search.best_params_)
ridge_cat_sc_gs.fit(X_train_cat_scaled, y_train)

print('----------------------------')

print('metrics:')
ridge_train_pred = ridge_cat_sc_gs.predict(X_train_cat_scaled)
ridge_test_pred = ridge_cat_sc_gs.predict(X_test_cat_scaled)

get_metrics(y_train, ridge_train_pred, y_test, ridge_test_pred)

best params:
{'alpha': 1000}
----------------------------
metrics:
R2 для трейна: 0.7684838798964527
R2 для теста: 0.781233686458571
MSE для трейна: 66361395969.545685
MSE для теста: 125753124035.36667


**Вывод**
- Да, r2 стал лучше на ~18п.п, что в целом отлично
- MSE улучишлось раза в ~2, что говорит, что вообщем есть улучшение качества

# **Часть 4 - бонусная (1 балл) | Feature Engineering**

В этой части домашнего задания вам предлагается проявить свою креативность для улучшения прогноза модели. Любые другие модели, кроме различных форм линейной (или полиномиальной) регресси, использовать запрещается. А значит, придется работать с признаками

**Что можно попробовать сделать?** (каждый пункт по 0.4 балла, но не больше 1-х балла в сумме)

1.   *Сгенерировать новые признаки на основе уже существующих:*
    * посчитать произведения // частные признаков (кажется, что посчитать число "лошадей" на литр объема может быть полезно);
    * имеет смысл обратить внимание на визуализации в части с EDA (к примеру, зависимость цены от года выглядит квадратичной, а не линейной; значит, квадрат года нам, скорее всего, принесет больше пользы)

2.   *Добыть новые признаки:*
    * имеем название автомобиля, которое никак не используем (можно спарсить инфу о классе автомобиля или каких-то специфических опциях)
    * можно добавить пороговые признаки вроде "владелец третий или больше" и объединить признаки в некоторые осмысленные правила, например "первый или второй владелец и продавец официальный дилер" (подбирать пороги удобно по диаграммам рассеяния)

3.   *Поработать с уже имеющимися:*
    * далеко не факт, что заполнить пропуск медианой было лучшей идеей (как минимум, можно добавить dummy-столбец для модели, сигнализирующий, что раньше на месте медианы был пропуск -- там где он был, конечно); попробуйте другие способы филлинга;
    * мы не анализировали, есть ли в данных выбросы => никак выбросы не обрабатывали; наиболее простым и, тем не менее, довольно полезным вариантом нахождения выбросов могут послужить boxplot'ы для каждого столбца; что делать с выбросами думайте сами :) -- вариантов довольно много
    * мы толком не смотрели на таргет сам по себе; в нем тоже могут быть неожиданности -- стоит хотя бы проверить
    * можно заметить, что некоторые признаки распределены совсем не нормально; возможно их стоит отлогарифмировать

И так далее...

Feel Free to Try!

In [75]:
X_train_new = X_train_cat.copy()
X_test_new = X_test_cat.copy()

# Возраст автомобиля
X_train_new['age'] = 2025 - X_train_new['year']
X_test_new['age'] = 2025 - X_test_new['year']

# Лошадиные силы на литр двигателя
X_train_new['power_per_engine'] = X_train_new['max_power'] / (X_train_new['engine'] + 1e-5)
X_test_new['power_per_engine'] = X_test_new['max_power'] / (X_test_new['engine'] + 1e-5)

# Взаимодействие пробега и возраста
X_train_new['km_age'] = X_train_new['km_driven'] * X_train_new['age']
X_test_new['km_age'] = X_test_new['km_driven'] * X_test_new['age']

# Полиномиальные признаки года (quadratic)
X_train_new['year2'] = X_train_new['year']**2
X_test_new['year2'] = X_test_new['year']**2

# Логарифмируем сильно скошенные признаки
X_train_new['log_km_driven'] = np.log1p(X_train_new['km_driven'])
X_test_new['log_km_driven'] = np.log1p(X_test_new['km_driven'])

X_train_new['log_selling_price'] = np.log1p(y_train)
X_test_new['log_selling_price'] = np.log1p(y_test)

# Масштабируем признаки
scaler = StandardScaler()
X_train_scaled = scaler.fit_transform(X_train_new)
X_test_scaled = scaler.transform(X_test_new)



In [103]:
X_test_new.to_csv('data.csv', index=False, encoding='utf-8')

In [76]:
# ElasticNet
param_grid = {
    'alpha': [0.0005, 0.001, 0.002],
    'l1_ratio': [0.7, 0.75, 0.8],
    'max_iter': [20000]
}

grid_search = GridSearchCV(
    estimator=ElasticNet(random_state=42),
    param_grid=param_grid,
    cv=10,
    scoring='r2',
)
grid_search.fit(X_train_scaled, y_train)

elastic_final = ElasticNet(**grid_search.best_params_)
elastic_final.fit(X_train_scaled, y_train)
print('best params:')
print(grid_search.best_params_)

print('----------------------------')

print('metrics:')
elastic_train_pred = elastic_final.predict(X_train_scaled)
elastic_test_pred = elastic_final.predict(X_test_scaled)

get_metrics(y_train, elastic_train_pred, y_test, elastic_test_pred)

best params:
{'alpha': 0.002, 'l1_ratio': 0.7, 'max_iter': 20000}
----------------------------
metrics:
R2 для трейна: 0.8269675794003415
R2 для теста: 0.8264790453051707
MSE для трейна: 49597725522.72904
MSE для теста: 99744799760.23268


**Вывод**
Все эти новые признаки направлены на то, чтобы линейная модель могла лучше захватывать нелинейные зависимости и взаимодействия признаков, которые напрямую влияют на цену автомобиля.

- Получилось:
  - улучшить r2 на ~10п.п.  
  - улучшить mse на ~25%

# **Часть 4. | Бизнесовая (0.5 балла)**

### **Задание 23 (0.25 балла)**

В мире бизнеса очень важно давать оценку качества модели понятную бизнесу, поэтому иногда заказчики приходят с кастомными метриками. Попробуем сделать такую для нашей задачи.

**Описание метрики:**

Среди всех предсказанных цен на авто нужно посчитать долю прогнозов, отличающихся от реальных цен на эти авто не более чем на 10% (в одну или другую сторону)

**Ваша задача:**

- [ ] Реализуйте метрику `business_metric`
- [ ] Посчитайте метрику для всех обученных моделей и определеите, какаю лучше всего решает задачу бизнеса

In [77]:
def business_metrics(y_true, y_pred):
    return float(np.mean(np.abs(y_true-y_pred) / y_true <= 0.1))

In [78]:
# Определяем функцию бизнес-метрики
def business_metrics(y_true, y_pred):
    return float(np.mean(np.abs(y_true - y_pred) / y_true <= 0.1))

# Список моделей и их предсказаний
models_preds = [
    ("LinearRegression", model_nums_train_pred, model_nums_test_pred),
    ("LinearRegression_scaled", model_nums_scaled_train_pred, model_nums_scaled_test_pred),
    ("Lasso_scaled", model_nums_scaled_lasso_train_pred, model_nums_scaled_lasso_test_pred),
    ("Lasso_scaled_optimal", model_nums_scaled_lasso_optimal_train_pred, model_nums_scaled_lasso_optimal_test_pred),
    ("Ridge_GridSearch", ridge_train_pred, ridge_test_pred),
    ("Ridge_new_features", elastic_train_pred, elastic_test_pred)  # модель с новыми признаками
]

# Вывод метрик для каждой модели
for name, train_pred, test_pred in models_preds:
    print(f"--- {name} ---")
    print(f"Train: R2 = {r2_score(y_train, train_pred):.4f}, MSE = {MSE(y_train, train_pred):.4f}, Business = {business_metrics(y_train, train_pred):.4f}")
    print(f"Test : R2 = {r2_score(y_test, test_pred):.4f}, MSE = {MSE(y_test, test_pred):.4f}, Business = {business_metrics(y_test, test_pred):.4f}")
    print()


--- LinearRegression ---
Train: R2 = 0.6023, MSE = 114005585965.9157, Business = 0.2176
Test : R2 = 0.6011, MSE = 229302674203.2037, Business = 0.2450

--- LinearRegression_scaled ---
Train: R2 = 0.6023, MSE = 114005585965.9157, Business = 0.2176
Test : R2 = 0.6011, MSE = 229302674203.1981, Business = 0.2450

--- Lasso_scaled ---
Train: R2 = 0.6023, MSE = 114005585979.6563, Business = 0.2176
Test : R2 = 0.6011, MSE = 229303390631.4193, Business = 0.2450

--- Lasso_scaled_optimal ---
Train: R2 = 0.6015, MSE = 114216197841.0670, Business = 0.2226
Test : R2 = 0.5951, MSE = 232743001622.9878, Business = 0.2420

--- Ridge_GridSearch ---
Train: R2 = 0.7685, MSE = 66361395969.5457, Business = 0.2723
Test : R2 = 0.7812, MSE = 125753124035.3667, Business = 0.3130

--- Ridge_new_features ---
Train: R2 = 0.8270, MSE = 49597725522.7290, Business = 0.3529
Test : R2 = 0.8265, MSE = 99744799760.2327, Business = 0.3450



### **Задание 24 (0.25 балла)**

Но у бизнеса не всегда есть идеи и иногда задача на выбор метрики делегируется вам.

**Задание:**

- [ ] Придумайте и реализуйте другую кастомную метрику с учетом того, что модель не должна сильно ошибаться в прогнозе, но недопрогноз для модели, согласно мнению бизнеса, хуже, чем перепрогноз.
- [ ] Посчитайте метрику для всех обученных моделей и определеите, какаю лучше всего решает задачу бизнеса



In [79]:
def truncated_business_metric(y_true, y_pred, cap=0.3, under_penalty=2.0):
    """
    Truncated loss
    cap: максимальная относительная ошибка, выше которой усекаем
    under_penalty: штраф за недооценку (y_pred < y_true)
    """
    error = (y_pred - y_true) / y_true
    truncated_error = np.clip(error, -cap, cap)

    mask_under = truncated_error < 0
    truncated_error[mask_under] *= under_penalty

    return float(np.mean(np.abs(truncated_error)))


models_preds = [
    ("LinearRegression", model_nums_train_pred, model_nums_test_pred),
    ("LinearRegression_scaled", model_nums_scaled_train_pred, model_nums_scaled_test_pred),
    ("Lasso_scaled", model_nums_scaled_lasso_train_pred, model_nums_scaled_lasso_test_pred),
    ("Lasso_scaled_optimal", model_nums_scaled_lasso_optimal_train_pred, model_nums_scaled_lasso_optimal_test_pred),
    ("Ridge_GridSearch", ridge_train_pred, ridge_test_pred),
    ("Ridge_new_features", elastic_train_pred, elastic_test_pred)  # модель с новыми признаками
    ]

# Вывод метрик для каждой модели
for name, train_pred, test_pred in models_preds:
    print(f"--- {name} ---")
    print(f"Train: R2 = {r2_score(y_train, train_pred):.4f}, MSE = {MSE(y_train, train_pred):.4f}, Business = {business_metrics(y_train, train_pred):.4f}, truncated_business_metric = {truncated_business_metric(y_train, train_pred):.4f}")
    print(f"Test : R2 = {r2_score(y_test, test_pred):.4f}, MSE = {MSE(y_test, test_pred):.4f}, Business = {business_metrics(y_test, test_pred):.4f}, truncated_business_metric = {truncated_business_metric(y_train, train_pred):.4f}")
    print()



--- LinearRegression ---
Train: R2 = 0.6023, MSE = 114005585965.9157, Business = 0.2176, truncated_business_metric = 0.3032
Test : R2 = 0.6011, MSE = 229302674203.2037, Business = 0.2450, truncated_business_metric = 0.3032

--- LinearRegression_scaled ---
Train: R2 = 0.6023, MSE = 114005585965.9157, Business = 0.2176, truncated_business_metric = 0.3032
Test : R2 = 0.6011, MSE = 229302674203.1981, Business = 0.2450, truncated_business_metric = 0.3032

--- Lasso_scaled ---
Train: R2 = 0.6023, MSE = 114005585979.6563, Business = 0.2176, truncated_business_metric = 0.3032
Test : R2 = 0.6011, MSE = 229303390631.4193, Business = 0.2450, truncated_business_metric = 0.3032

--- Lasso_scaled_optimal ---
Train: R2 = 0.6015, MSE = 114216197841.0670, Business = 0.2226, truncated_business_metric = 0.2999
Test : R2 = 0.5951, MSE = 232743001622.9878, Business = 0.2420, truncated_business_metric = 0.2999

--- Ridge_GridSearch ---
Train: R2 = 0.7685, MSE = 66361395969.5457, Business = 0.2723, truncated

- Модель не должна сильно ошибаться — за это отвечает усечение ошибок сверху (cap). Ошибки, превышающие заданный порог, не влияют чрезмерно на метрику, что предотвращает «порчу» оценки из-за аномальных значений.

- Недопрогноз хуже перепрогноза — за это отвечает параметр under_penalty. Отрицательные ошибки (когда модель недооценила цену) умножаются на коэффициент >1, усиливая штраф.

- Там нет особых различий в метриках на первых итерациях. Шо мы лассо использовали, шо тюнили гип-ы. Это вообще не корректно ожидать улучшение при такой стратегии. Features first - золотое правило.

# **<font color="green">Часть 5 | Создание интерактивного приложения на Streamlit (3 балла)</font>**

Вам необходимо создать интерактивное приложение на Streamlit, которое будет:

- Показывать основные информативные графики/гистограммы в рамках EDA (1 балл)
- На вход запрашивать csv-файл с признаками объектов или запрашивать признаки объекта в окошках для ввода, и применять на поступивших объектах модель (1 балл)
- Визуализировать веса обученной модели (1 балл)

ВСЕ ВЗЯЛ ИЗ НОУТБКА ЗАНЯТИЯ

In [88]:
model_dir = 'models'
os.makedirs(model_dir, exist_ok=True)

print(f"📁 Директория '{model_dir}' создана или уже существует")

📁 Директория 'models' создана или уже существует


In [94]:
# Сохранение модели через Pickle
print("💾 Сохраняем модель через Pickle...")
print("-" * 60)

# Путь к файлу модели
model_path = os.path.join(model_dir, 'price_predict_model.pkl')

# ВАЖНО: открываем файл в бинарном режиме ('wb' = write binary)
# Это обязательно для pickle!

with open(model_path, 'wb') as f:
    # pickle.dump() сериализует объект модели и записывает в файл
    # protocol=HIGHEST_PROTOCOL - берет самый актуальный протокол
    
    pickle.dump(elastic_final, f, protocol=pickle.HIGHEST_PROTOCOL)

print(f"✅ Модель сохранена: {model_path}")
print(f"   Размер файла: {os.path.getsize(model_path) / 1024:.2f} KB")
print(f"   Количество признаков: {len(X_train_new.columns)}")
print("-" * 60)
print("🎉 Модель успешно сохранена через Pickle!")

# Также сохраним список признаков отдельно для удобства
feature_names_path = os.path.join(model_dir, 'feature_names.pkl')
with open(feature_names_path, 'wb') as f:
    pickle.dump(X_train_new.columns, f, protocol=4)
print(f"✅ Список признаков сохранен: {feature_names_path}")

💾 Сохраняем модель через Pickle...
------------------------------------------------------------
✅ Модель сохранена: models/price_predict_model.pkl
   Размер файла: 1.00 KB
   Количество признаков: 62
------------------------------------------------------------
🎉 Модель успешно сохранена через Pickle!
✅ Список признаков сохранен: models/feature_names.pkl


In [95]:
# Проверка: загрузка и тестирование модели через Pickle
print("🔍 Проверяем загрузку модели через Pickle...\n")

# Загружаем модель: ВАЖНО - открываем файл в бинарном режиме ('rb' = read binary)
with open(model_path, 'rb') as f:
    loaded_model = pickle.load(f)

# Загружаем список признаков
with open(feature_names_path, 'rb') as f:
    loaded_features = pickle.load(f)

print("✅ Модель успешно загружена через Pickle!")
print(f"\nТип модели: {type(loaded_model).__name__}")
print(f"Количество признаков: {len(loaded_features)}\n")

print(f"Список признаков: ")

print(loaded_features)

🔍 Проверяем загрузку модели через Pickle...

✅ Модель успешно загружена через Pickle!

Тип модели: ElasticNet
Количество признаков: 62

Список признаков: 
Index(['year', 'km_driven', 'mileage', 'engine', 'max_power', 'torque',
       'max_torque_rpm', 'fuel_Diesel', 'fuel_LPG', 'fuel_Petrol',
       'seller_type_Individual', 'seller_type_Trustmark Dealer',
       'transmission_Manual', 'owner_Fourth & Above Owner',
       'owner_Second Owner', 'owner_Test Drive Car', 'owner_Third Owner',
       'name_Ashok', 'name_Audi', 'name_BMW', 'name_Chevrolet', 'name_Daewoo',
       'name_Datsun', 'name_Fiat', 'name_Force', 'name_Ford', 'name_Honda',
       'name_Hyundai', 'name_Isuzu', 'name_Jaguar', 'name_Jeep', 'name_Kia',
       'name_Land', 'name_Lexus', 'name_MG', 'name_Mahindra', 'name_Maruti',
       'name_Mercedes-Benz', 'name_Mitsubishi', 'name_Nissan', 'name_Opel',
       'name_Peugeot', 'name_Renault', 'name_Skoda', 'name_Tata',
       'name_Toyota', 'name_Volkswagen', 'name_Volvo', '

# **Часть 6 | Оформление репозитория и оценка сервиса (3 балла)**

**Результаты вашей работы** необходимо разместить в своём GitHub-репозитории. В этот же репозиторий позже будет добавлена вторая часть.

Под результатами первой части понимаем следующее:

---

### Обязательные файлы:

1. **`.ipynb`-ноутбук** со всеми экспериментами:

   * полный EDA,
   * все шаги препроцессинга,
   * обучение и сравнение моделей,
   * сохранённые output’ы.

2. **`.pickle`-файл**, содержащий:

   * обученную модель (или пайплайн `scaler + model`);
   * параметры скейлинга;
   * любые числовые объекты, необходимые для инференса внутри Streamlit-приложения.

3. **`.md`-файл с выводами** о проделанной работе:

   * что было сделано (краткое описание каждого этапа);
   * какие результаты были получены (метрики + интерпретация);
   * что дало наибольший прирост качества;
   * что сделать не удалось и почему (это нормально и даже полезно);
   * **оценка разработанного сервиса**:

     * насколько приложение удобно в использовании;
     * что получилось визуализировать хорошо, а что — менее удачно;
     * какие ограничения или проблемы вы заметили;
     * какие улучшения планируете в следующей итерации.

По результатам второй части, ждем:

4. **Streamlit-приложение** (например, `app.py`), которое можно запустить командой:

   ```bash
   streamlit run app.py
   ```

В приложении должно быть:

* отображение ключевых графиков EDA;
* ввод данных (CSV или ручной ввод);
* применение модели;
* визуализация весов/коэффициентов.

**И ссылку на приложение в StreamlitHub.**


### **За что могут быть сняты баллы:**

* отсутствие `.pickle` с моделью / пайплайном;
* слабая или неполная аналитика в `.md`-файле;
* беспорядок в ноутбуке или неясная логика вычислений;
* отсутствие возможности запустить Streamlit-приложение.
